In [3]:
import pandas as pd
import numpy as np
import json
import gzip
import seaborn as sns
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer, TfidfVectorizer
import re
import string
import nltk
import re

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [6]:
!wget http://deepyeti.ucsd.edu/jianmo/amazon/metaFiles/meta_Video_Games.json.gz

--2020-05-17 12:47:44--  http://deepyeti.ucsd.edu/jianmo/amazon/metaFiles/meta_Video_Games.json.gz
Resolving deepyeti.ucsd.edu (deepyeti.ucsd.edu)... 169.228.63.50
Connecting to deepyeti.ucsd.edu (deepyeti.ucsd.edu)|169.228.63.50|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 80222877 (77M) [application/octet-stream]
Saving to: ‘meta_Video_Games.json.gz’

meta_Video_Games.js 100%[===================>]  76.51M  4.61MB/s    in 17s     

2020-05-17 12:48:02 (4.39 MB/s) - ‘meta_Video_Games.json.gz’ saved [80222877/80222877]



In [0]:
data = []
with gzip.open('meta_Video_Games.json.gz') as f:
    for l in f:
        data.append(json.loads(l.strip()))

In [0]:
df = pd.DataFrame.from_dict(data)

In [9]:
!wget http://deepyeti.ucsd.edu/jianmo/amazon/categoryFilesSmall/Video_Games_5.json.gz

--2020-05-17 12:48:10--  http://deepyeti.ucsd.edu/jianmo/amazon/categoryFilesSmall/Video_Games_5.json.gz
Resolving deepyeti.ucsd.edu (deepyeti.ucsd.edu)... 169.228.63.50
Connecting to deepyeti.ucsd.edu (deepyeti.ucsd.edu)|169.228.63.50|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 154050105 (147M) [application/octet-stream]
Saving to: ‘Video_Games_5.json.gz’

Video_Games_5.json. 100%[===================>] 146.91M  5.39MB/s    in 28s     

2020-05-17 12:48:39 (5.27 MB/s) - ‘Video_Games_5.json.gz’ saved [154050105/154050105]



In [0]:
data2 = []
with gzip.open('Video_Games_5.json.gz') as f:
    for l in f:
        data2.append(json.loads(l.strip()))

In [0]:
df2 = pd.DataFrame.from_dict(data2)
df2 = df2[["reviewerID","asin","reviewText", "summary" ,"overall"]]
df2.drop_duplicates(keep=False , inplace = True)

In [0]:
df3 = pd.merge(df, df2, on="asin", how='right')

In [0]:
df4 = df3.groupby("asin").agg({"overall":"mean", "reviewerID":"count"})
df4["avg_rating"]= df4.overall
df4["Count"]= df4.reviewerID

In [0]:
df5 = pd.merge(df3, df4, on="asin", how='inner')

In [0]:
df5 = df5[["category","title","asin","reviewerID_x","overall_x","reviewText","summary","avg_rating","Count","brand","feature","description"]]

In [16]:
df5.head()

category  ...                                        description
0  [Video Games, PC, Games]  ...  [ANNO 2070BRAND NEW - IN STOCKDVD Rom Software...
1  [Video Games, PC, Games]  ...  [ANNO 2070BRAND NEW - IN STOCKDVD Rom Software...
2  [Video Games, PC, Games]  ...  [ANNO 2070BRAND NEW - IN STOCKDVD Rom Software...
3  [Video Games, PC, Games]  ...  [ANNO 2070BRAND NEW - IN STOCKDVD Rom Software...
4  [Video Games, PC, Games]  ...  [ANNO 2070BRAND NEW - IN STOCKDVD Rom Software...

[5 rows x 12 columns]

In [0]:
df7 = df5.groupby("reviewerID_x").agg({"asin":"count"})
df7["user_count"] = df7.asin

In [0]:
df6 = pd.merge(df5, df7, on="reviewerID_x", how='inner')

In [19]:
df6.dropna(inplace = True)
df6= df6.reset_index()
df6.head(10)

index                                           category  ... asin_y user_count
0      0                           [Video Games, PC, Games]  ...     27         27
1      1  [Video Games, Retro Gaming & Microconsoles, Ni...  ...     27         27
2      2  [Video Games, Retro Gaming & Microconsoles, Ni...  ...     27         27
3      3  [Video Games, PC, Accessories, Controllers, Ga...  ...     27         27
4      4  [Video Games, PC, Accessories, Controllers, Ga...  ...     27         27
5      5                                 [Video Games, Wii]  ...     27         27
6      7         [Video Games, Kids & Family, Wii, Games, ]  ...     27         27
7      8                         [Video Games, PC, Games, ]  ...     27         27
8      9  [Video Games, Wii, , Wii Wired Sensor Bar Only...  ...     27         27
9     10                         [Video Games, Nintendo DS]  ...     27         27

[10 rows x 15 columns]

In [0]:
del(df2,df3,df4,df5,df7)

In [0]:
df6['info'] = df6.category  + df6.feature 

In [0]:
def clean(i):
  b = re.sub("\n", "",i)
  b = re.sub(' ', '',b)
  return b
  df6.brand.loc[i]= b.split(' ')

In [0]:
df_user = df6.drop_duplicates(subset=["asin_x","reviewerID_x","user_count"])
df_user.reset_index(inplace = True)

In [24]:
df_user.user_count.describe()

count    403163.000000
mean         23.955135
std          67.784215
min           1.000000
25%           6.000000
50%          10.000000
75%          18.000000
max        1054.000000
Name: user_count, dtype: float64

In [25]:
df_user = df_user[["asin_x","reviewerID_x"]]
df_user.head()


asin_x    reviewerID_x
0  0700026657  A1HP7NVNPFMA4N
1  B00000JMWB  A1HP7NVNPFMA4N
2  B0000ALFCI  A1HP7NVNPFMA4N
3  B0009VXBAQ  A1HP7NVNPFMA4N
4  B000FQ9QVI  A1HP7NVNPFMA4N

In [0]:
user_list ={}
for i in range(df_user.shape[0]):
  if df_user.reviewerID_x.loc[i] in user_list:
    user_list[df_user.reviewerID_x.loc[i]].append(df_user.asin_x.loc[i])
  else:
    user_list[df_user.reviewerID_x.loc[i]] = [df_user.asin_x.loc[i]]


In [0]:
df_prd = df6.drop_duplicates(subset=["asin_x","Count"])

In [28]:
df_prd.Count.describe()

count    14776.000000
mean        31.274973
std         53.067352
min          1.000000
25%          8.000000
50%         14.000000
75%         32.000000
max        806.000000
Name: Count, dtype: float64

In [29]:
df6.shape

(461859, 16)

In [0]:
df6["data"] = df6["info"].apply(lambda x: " ".join(x))

In [0]:
df6.drop_duplicates(subset =["asin_x", "data"], inplace = True)

In [0]:
!pip install nltk

In [32]:
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [0]:
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
def get_data(df):
    word_list = df.split(" ")
    new_wrd_list =  [lemmatizer.lemmatize(i) for i in word_list]
    return ' '.join(new_wrd_list)
df6["clean_data"] = df6["data"].apply(get_data)

In [0]:
'''reviews = df6["data"] 
countVector = CountVectorizer(max_features = 300, stop_words='english',) 
transformedReviews = countVector.fit_transform(reviews) 

dfReviews = pd.DataFrame(transformedReviews.A, columns=countVector.get_feature_names())
dfReviews = dfReviews.astype(int)'''

In [0]:
from tqdm.notebook import tqdm

In [0]:
tf = TfidfVectorizer(analyzer='word',ngram_range=(1, 2),min_df=0, stop_words='english')
tfidf_matrix = tf.fit_transform(df6['clean_data'])

In [0]:
df6.reset_index(inplace = True)

In [0]:
df6.asin_x

In [0]:

indices = pd.Series(df6.index, index=df6['asin_x'])

In [37]:
indices
indices.loc['B00000JMWB']

1

In [0]:
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity
cosine_sim = linear_kernel(tfidf_matrix, tfidf_matrix)

In [0]:
asin_to_title = dict(zip(df6.asin_x, df6.title))
asin_to_avgscore = dict(zip(df6.asin_x, df6.avg_rating))

In [40]:
cosine_sim.shape

(14776, 14776)

In [0]:
def get_rec(prd, df):
  id = indices.loc[prd]
  sim_scores = list(enumerate(cosine_sim[id]))
  sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)
  sim_scores = sim_scores[1:11]
  prd_ids = [i[0] for i in sim_scores]
  rec = [df.asin_x.loc[i] for i in prd_ids]
  rec= sorted(rec, key = lambda x :asin_to_avgscore[x], reverse = True)
  return rec

In [0]:
def get_combined_rec(prds):
  freq ={}
  for item in prds:
    for i in item:
      freq[i]= prds.count(i)
    freq_final = sorted(freq, key = lambda x: freq[x], reverse = True)
  return list(freq_final[:10])

In [63]:

for user in user_list.keys():
  rec_list_per_prd=[]
  for prd in user_list[user]:
    rec_list_per_prd.append(get_rec(prd,df6))
    #print(rec_list_per_prd)
  recommendations= get_combined_rec(rec_list_per_prd) 

  print("The purchase history is",[asin_to_title[t] for t in user_list[user]])
  print("the rec are ", [asin_to_title[t] for t in recommendations])
  print("---------------------------------------------------------------------------------------------------------------------------")

The purchase history is ['Anno 2070', 'Hexen', 'Logitech Dual Action Game Pad USB', 'Wii', 'Super Mario Galaxy', 'Age Of Mythology:  Titans - PC', 'var aPageStart = (new Date()).getTime();\nvar ue_t0=ue_t0||+new Date();\n\nwindow.ue_ihb = (window.ue_ihb || window.ueinit || 0) + 1;\nif (window.ue_ihb === 1) {\n\nvar ue_csm = window,\n    ue_hob = +new Date();\n(function(d){var e=d.ue=d.ue||{},f=Date.now||function(){return+new Date};e.d=function(b){return f()-(b?0:d.ue_t0)};e.stub=function(b,a){if(!b[a]){var c=[];b[a]=function(){c.push([c.slice.call(arguments),e.d(),d.ue_id])};b[a].replay=function(b){for(var a;a=c.shift();)b(a[0],a[1],a[2])};b[a].isStub=1}};e.exec=function(b,a){return function(){if(1==window.ueinit)try{return b.apply(this,arguments)}catch(c){ueLogError(c,{attribution:a||"undefined",logLevel:"WARN"})}}}})(ue_csm);\n\n\n    var ue_err_chan = \'jserr-rw\';\n(function(d,e){function h(f,b){if(!(a.ec>a.mxe)&&f){a.ter.push(f);b=b||{};var c=f.logLevel||b.logLevel;c&&c!==k&&c!==m

KeyboardInterrupt: ignored

In [0]:
l=[1,2,1,2,3,4,3,4,4,4,4]
feq ={}
for i in l:
  feq[i] = l.count(i)


In [46]:
feq

{1: 2, 2: 2, 3: 2, 4: 5}